# Harvard USPTO Dataset Training

## Importing Packages

We first need to import the actual USPTO dataset.

In [1]:
!pip install datasets

In [2]:
from datasets import load_dataset
import pandas as pd
import numpy as np

## Loading the Dataset

We need to extract the dataset. We filter only for those in January 2016.

In [3]:
dataset_dict = load_dataset('HUPD/hupd',
    name='sample',
    data_files="https://huggingface.co/datasets/HUPD/hupd/blob/main/hupd_metadata_2022-02-22.feather", 
    icpr_label=None,
    train_filing_start_date='2016-01-01',
    train_filing_end_date='2016-01-21',
    val_filing_start_date='2016-01-22',
    val_filing_end_date='2016-01-31',
)

Found cached dataset hupd (/home/jovyan/.cache/huggingface/datasets/HUPD___hupd/sample-a4eeba92b4229e93/0.0.0/6920d2def8fd7767046c0470603357f76866e5a09c97e19571896bfdca521142)


  0%|          | 0/2 [00:00<?, ?it/s]

We print out the dataset to understand what exactly we want to look for

In [4]:
print(dataset_dict)

DatasetDict({
    train: Dataset({
        features: ['patent_number', 'decision', 'title', 'abstract', 'claims', 'background', 'summary', 'description', 'cpc_label', 'ipc_label', 'filing_date', 'patent_issue_date', 'date_published', 'examiner_id'],
        num_rows: 16153
    })
    validation: Dataset({
        features: ['patent_number', 'decision', 'title', 'abstract', 'claims', 'background', 'summary', 'description', 'cpc_label', 'ipc_label', 'filing_date', 'patent_issue_date', 'date_published', 'examiner_id'],
        num_rows: 9094
    })
})


We separate our data between training and validation

In [5]:
df_train = pd.DataFrame(dataset_dict['train'] )
df_val = pd.DataFrame(dataset_dict['validation'] )

We can preview the training data

In [6]:
df_train

patent_number  decision  \
0          13261748  ACCEPTED   
1          13995128  ACCEPTED   
2          14241799   PENDING   
3          14348792  ACCEPTED   
4          14360978  REJECTED   
...             ...       ...   
16148      15002394  ACCEPTED   
16149      15002396  REJECTED   
16150      15330955  REJECTED   
16151      15330961   PENDING   
16152      15330968   PENDING   

                                                   title  \
0                    MINI-OPTICAL NETWORK TERMINAL (ONT)   
1      APPARATUS FOR FORMING AND READING AN IDENTIFIC...   
2                                PORTABLE DRUG DISPENSER   
3                           LIQUID-COOLED HEAT EXCHANGER   
4                                SOLE MEMBER OF FOOTWEAR   
...                                                  ...   
16148  ROBOT HAND CONTROLLING METHOD AND ROBOTICS DEVICE   
16149    IMMUNOGLOBULIN FUSION PROTEINS AND USES THEREOF   
16150                               PIPE EXTRACTION TOOL   
16151  Molded parts with thermoplastic cellulose biop...   
16152        Transmission method with double directivity   

                                                abstract  \
0      The present invention relates to passive optic...   
1      Embodiments of the invention provide a method ...   
2      A portable drug dispenser includes a chamber f...   
3      A crystal growth furnace comprising a crucible...   
4      A shoe midsole is composed of a base plate (1)...   
...                                                  ...   
16148  A robot hand controlling method executes calcu...   
16149  A fusion protein is disclosed. The fusion prot...   
16150  A pipe extraction tool that grips the inside o...   
16151  A longitudinal extending body with oriented fi...   
16152  A transmission method using a massive MIMO (Mu...   

                                                  claims  \
0      1. A compact optical network terminal, compris...   
1      1. A method comprising: using a first reader t...   
2      1. A portable drug dispenser, comprising: a ch...   
3      1. A crystal growth furnace for growing a crys...   
4      1. A sole member of footwear comprising a base...   
...                                                  ...   
16148  1. A controlling method of a robot hand, the r...   
16149  1. A fusion protein comprising an Fc fragment ...   
16150  1. A pipe extraction tool for extracting a pip...   
16151  1. A longitudinal body of a solidified organic...   
16152  1. Transmission method with double directivity...   

                                              background  \
0      <SOH> BACKGROUND OF THE INVENTION <EOH>A netwo...   
1      <SOH> BACKGROUND OF THE INVENTION <EOH>Identif...   
2                                                          
3      <SOH> BACKGROUND OF THE INVENTION <EOH>1. Fiel...   
4      <SOH> BACKGROUND ART <EOH>When the heel touche...   
...                                                  ...   
16148  <SOH> BACKGROUND OF THE INVENTION <EOH>1. Fiel...   
16149  <SOH> BACKGROUND OF THE INVENTION <EOH>An immu...   
16150  <SOH> BACKGROUND OF THE INVENTION <EOH>1. Fiel...   
16151  <SOH> BACKGROUND OF INVENTION <EOH>In the medi...   
16152            <SOH> BACKGROUND OF THE INVENTION <EOH>   

                                                 summary  \
0      <SOH> SUMMARY OF THE INVENTION <EOH>An aspect ...   
1      <SOH> SUMMARY OF THE INVENTION <EOH>In accorda...   
2                                                          
3      <SOH> SUMMARY OF THE INVENTION <EOH>The presen...   
4      <SOH> BRIEF DESCRIPTION OF THE DRAWINGS <EOH>F...   
...                                                  ...   
16148  <SOH> SUMMARY OF THE INVENTION <EOH>An object ...   
16149  <SOH> SUMMARY OF THE INVENTION <EOH>The presen...   
16150  <SOH> BRIEF SUMMARY OF THE INVENTION <EOH>The ...   
16151  <SOH> BRIEF SUMMARY OF THE PRESENT INVENTION <...   
16152  <SOH> BRIEF SUMMARY OF THE INVENTION <EOH>The ...   

    

## Pre-Processing the Data

We are interested in the following columns:
- Abstract
- Claims
- Decision <- our `y`

Let's preprocess them both out of our training and validation data

Also, consider that the "Decision" column has three types of values: "Accepted", "Rejected", and "Pending". To remove unecessary baggage, we will be only looking for "Accepted" and "Rejected".

In [7]:
necessary_columns = ["abstract","claims","decision"]
output_values = ['ACCEPTED','REJECTED'] 

In [8]:
trainFeaturesToDrop = [col for col in list(df_train.columns) if col not in necessary_columns]
trainDF = df_train.dropna()
trainDF.drop(columns=trainFeaturesToDrop, inplace=True)
trainDF = trainDF[trainDF['decision'].isin(output_values)]

In [9]:
trainDF

decision                                           abstract  \
0      ACCEPTED  The present invention relates to passive optic...   
1      ACCEPTED  Embodiments of the invention provide a method ...   
3      ACCEPTED  A crystal growth furnace comprising a crucible...   
4      REJECTED  A shoe midsole is composed of a base plate (1)...   
5      ACCEPTED  A ratchet tool includes a shaft member, a hand...   
...         ...                                                ...   
16144  ACCEPTED  A wavelength tunable laser device, including: ...   
16145  ACCEPTED  In one aspect, a method for use in preparing a...   
16148  ACCEPTED  A robot hand controlling method executes calcu...   
16149  REJECTED  A fusion protein is disclosed. The fusion prot...   
16150  REJECTED  A pipe extraction tool that grips the inside o...   

                                                  claims  
0      1. A compact optical network terminal, compris...  
1      1. A method comprising: using a first reader t...  
3      1. A crystal growth furnace for growing a crys...  
4      1. A sole member of footwear comprising a base...  
5      1. A ratchet tool, comprising a shaft member, ...  
...                                                  ...  
16144  1. A wavelength tunable laser device, comprisi...  
16145  1. (canceled) 2. The method of claim 19, where...  
16148  1. A controlling method of a robot hand, the r...  
16149  1. A fusion protein comprising an Fc fragment ...  
16150  1. A pipe extraction tool for extracting a pip...  

[8719 rows x 3 columns]

In [10]:
valFeaturesToDrop = [col for col in list(df_val.columns) if col not in necessary_columns]
valDF = df_val.dropna()
valDF.drop(columns=valFeaturesToDrop, inplace=True)
valDF = valDF[valDF['decision'].isin(output_values)]

In [11]:
valDF

decision                                           abstract  \
0     REJECTED  Regimen for the treatment of rosacea include t...   
1     ACCEPTED  A clamp arrangement includes a pair of bracket...   
2     REJECTED  A system and method for device action and conf...   
4     REJECTED  Systems and methods for managing datasets prod...   
9     ACCEPTED  A scan driving circuit is provided. The scan d...   
...        ...                                                ...   
9085  REJECTED  The non-rigid gate device as described may be ...   
9090  REJECTED  The present invention provides an improved unc...   
9091  ACCEPTED  A method for detecting a software-race conditi...   
9092  ACCEPTED  The present application relates to multi-stage...   
9093  ACCEPTED  A paper feeder includes a housing, a driving u...   

                                                 claims  
0     1. A treatment regimen comprising: cleansing a...  
1     1. A clamp arrangement for supporting a fractu...  
2     1-20. (canceled) 21. A mobile device comprisin...  
4     1. A method, comprising: executing, by one or ...  
9     1. A scan driving circuit for driving a scan l...  
...                                                 ...  
9085  1; A non-rigid blocking apparatus referred to ...  
9090  1. A method for rendering a plastic surface am...  
9091  1. A method for detecting a software-race cond...  
9092  1. A multi-stage amplitude modulation-based me...  
9093  1. A paper feeder, comprising: a housing; a dr...  

[4888 rows x 3 columns]

We need to replace the values in the `decision` column to numerical representations. We will set "ACCEPTED" as `1` and "REJECTED" as `0`.

In [12]:
yKey = {"ACCEPTED":1,"REJECTED":0}

In [13]:
trainDF2 = trainDF.replace({"decision": yKey})
valDF2 = valDF.replace({"decision": yKey})

In [14]:
trainDF2

decision                                           abstract  \
0             1  The present invention relates to passive optic...   
1             1  Embodiments of the invention provide a method ...   
3             1  A crystal growth furnace comprising a crucible...   
4             0  A shoe midsole is composed of a base plate (1)...   
5             1  A ratchet tool includes a shaft member, a hand...   
...         ...                                                ...   
16144         1  A wavelength tunable laser device, including: ...   
16145         1  In one aspect, a method for use in preparing a...   
16148         1  A robot hand controlling method executes calcu...   
16149         0  A fusion protein is disclosed. The fusion prot...   
16150         0  A pipe extraction tool that grips the inside o...   

                                                  claims  
0      1. A compact optical network terminal, compris...  
1      1. A method comprising: using a first reader t...  
3      1. A crystal growth furnace for growing a crys...  
4      1. A sole member of footwear comprising a base...  
5      1. A ratchet tool, comprising a shaft member, ...  
...                                                  ...  
16144  1. A wavelength tunable laser device, comprisi...  
16145  1. (canceled) 2. The method of claim 19, where...  
16148  1. A controlling method of a robot hand, the r...  
16149  1. A fusion protein comprising an Fc fragment ...  
16150  1. A pipe extraction tool for extracting a pip...  

[8719 rows x 3 columns]

In [15]:
valDF2

decision                                           abstract  \
0            0  Regimen for the treatment of rosacea include t...   
1            1  A clamp arrangement includes a pair of bracket...   
2            0  A system and method for device action and conf...   
4            0  Systems and methods for managing datasets prod...   
9            1  A scan driving circuit is provided. The scan d...   
...        ...                                                ...   
9085         0  The non-rigid gate device as described may be ...   
9090         0  The present invention provides an improved unc...   
9091         1  A method for detecting a software-race conditi...   
9092         1  The present application relates to multi-stage...   
9093         1  A paper feeder includes a housing, a driving u...   

                                                 claims  
0     1. A treatment regimen comprising: cleansing a...  
1     1. A clamp arrangement for supporting a fractu...  
2     1-20. (canceled) 21. A mobile device comprisin...  
4     1. A method, comprising: executing, by one or ...  
9     1. A scan driving circuit for driving a scan l...  
...                                                 ...  
9085  1; A non-rigid blocking apparatus referred to ...  
9090  1. A method for rendering a plastic surface am...  
9091  1. A method for detecting a software-race cond...  
9092  1. A multi-stage amplitude modulation-based me...  
9093  1. A paper feeder, comprising: a housing; a dr...  

[4888 rows x 3 columns]

We combine the `abstract` and `claims` columns into a single `text` column. We also re-label the `decision` column to `label`.

In [16]:
trainDF3 = trainDF2.rename(columns={'decision': 'label'})
trainDF3['text'] = trainDF3['abstract'] + ' ' + trainDF3['claims']
trainDF3.drop(columns=["abstract","claims"],inplace=True)
trainDF3

label                                               text
0          1  The present invention relates to passive optic...
1          1  Embodiments of the invention provide a method ...
3          1  A crystal growth furnace comprising a crucible...
4          0  A shoe midsole is composed of a base plate (1)...
5          1  A ratchet tool includes a shaft member, a hand...
...      ...                                                ...
16144      1  A wavelength tunable laser device, including: ...
16145      1  In one aspect, a method for use in preparing a...
16148      1  A robot hand controlling method executes calcu...
16149      0  A fusion protein is disclosed. The fusion prot...
16150      0  A pipe extraction tool that grips the inside o...

[8719 rows x 2 columns]

In [17]:
valDF3 = valDF2.rename(columns={'decision': 'label'})
valDF3['text'] = valDF3['abstract'] + ' ' + valDF3['claims']
valDF3.drop(columns=["abstract","claims"],inplace=True)
valDF3

label                                               text
0         0  Regimen for the treatment of rosacea include t...
1         1  A clamp arrangement includes a pair of bracket...
2         0  A system and method for device action and conf...
4         0  Systems and methods for managing datasets prod...
9         1  A scan driving circuit is provided. The scan d...
...     ...                                                ...
9085      0  The non-rigid gate device as described may be ...
9090      0  The present invention provides an improved unc...
9091      1  A method for detecting a software-race conditi...
9092      1  The present application relates to multi-stage...
9093      1  A paper feeder includes a housing, a driving u...

[4888 rows x 2 columns]

We can grab the data for each column so that we have a list of values for training labels, training texts, validation labels, and validation texts.

In [18]:
trainLabels = trainDF3["label"].tolist()
trainText = trainDF3["text"].tolist()

valLabels = valDF3["label"].tolist()
valText = valDF3["text"].tolist()

## Loading the Trainer

Now we can start training! This time, we will just go with `distilbert-base-uncased` for simplicity.

In [19]:
!pip install torch
!pip install transformers

In [20]:
import torch
from torch.utils.data import Dataset
from transformers import DistilBertTokenizerFast, DistilBertForSequenceClassification
from transformers import Trainer, TrainingArguments

In [21]:
model_name = "distilbert-base-uncased"
class USPTODataset(Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels
    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encoding.items()}
        item['labels'] = torch.tensor(self.labels[idx])
        return item
    def __len__(self):
        return len(self.labels)


In [22]:
tokenizer = DistilBertTokenizerFast.from_pretrained(model_name)

In [ ]:
train_encodings = tokenizer(trainText, truncation=True, padding=True)
val_encodings = tokenizer(valText, truncation=True, padding=True)

train_dataset = USPTODataset(train_encodings, trainLabels)
val_dataset = USPTODataset(val_encodings, valLabels)

train_args = TrainingArguments(
    output_dir="./results",
    num_train_epochs=2,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    warmup_steps=500,
    learning_rate=5e-5,
    weight_decay=0.01,
    logging_dir="./logs",
    logging_steps=10
)